In [2]:
import pandas as pd

In [3]:
df=pd.read_csv('train.csv')

In [4]:
df.head()

id                                              title              author  \
0   0  House Dem Aide: We Didn’t Even See Comey’s Let...       Darrell Lucus   
1   1  FLYNN: Hillary Clinton, Big Woman on Campus - ...     Daniel J. Flynn   
2   2                  Why the Truth Might Get You Fired  Consortiumnews.com   
3   3  15 Civilians Killed In Single US Airstrike Hav...     Jessica Purkiss   
4   4  Iranian woman jailed for fictional unpublished...      Howard Portnoy   

                                                text  label  
0  House Dem Aide: We Didn’t Even See Comey’s Let...      1  
1  Ever get the feeling your life circles the rou...      0  
2  Why the Truth Might Get You Fired October 29, ...      1  
3  Videos 15 Civilians Killed In Single US Airstr...      1  
4  Print \nAn Iranian woman has been sentenced to...      1

In [5]:
df.shape

(20800, 5)

In [6]:
df=df.dropna()
df.shape

(18285, 5)

In [7]:
X=df.drop('label',axis=1)

In [8]:
y=df['label']

In [9]:
import tensorflow as tf

In [16]:
from tensorflow.keras.layers import Embedding
from tensorflow.keras.preprocessing.sequence import pad_sequences
from tensorflow.keras.models import Sequential
from tensorflow.keras.preprocessing.text import one_hot
from tensorflow.keras.layers import LSTM
from tensorflow.keras.layers import Dense

In [17]:
voc_size=5000

## One Hot Representation

In [18]:
m=X.copy()

In [20]:
m.reset_index(inplace=True)

In [21]:
import re
import nltk
nltk.download('stopwords')
from nltk.corpus import stopwords

[nltk_data] Downloading package stopwords to
[nltk_data]     C:\Users\Hashtag\AppData\Roaming\nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


In [22]:
#data preprocessing(cleaning the data)
import re
from nltk.corpus import stopwords
from nltk.stem.porter import PorterStemmer
ps=PorterStemmer()
corpus=[]
for i in range(0,len(m)):
    review1=re.sub('[^a-z-A-Z]',' ',m['title'][i])
    review1=review1+ ' '
    review2=re.sub('[^a-z-A-Z]',' ',m['text'][i])
    review=(review1+review2)
    review=review.lower()
    review=review.split()
    review=[ps.stem(word) for word in review if not word in stopwords.words('english')]
    review=' '.join(review)
    corpus.append(review)


In [24]:
one_hot_repr=[one_hot(words,voc_size)for words in corpus]
one_hot_repr

[[2582,
  3754,
  3639,
  2657,
  3500,
  551,
  477,
  2205,
  290,
  3962,
  2582,
  3754,
  3639,
  2657,
  3500,
  551,
  477,
  2205,
  290,
  3962,
  1297,
  4428,
  344,
  217,
  2205,
  290,
  4678,
  3868,
  707,
  3309,
  2023,
  2911,
  4015,
  3684,
  3574,
  635,
  3793,
  3742,
  1567,
  1680,
  509,
  4040,
  2781,
  1164,
  728,
  2460,
  823,
  2103,
  2890,
  3376,
  551,
  86,
  2582,
  4104,
  3639,
  2850,
  2986,
  3472,
  664,
  1455,
  1164,
  728,
  1657,
  2364,
  551,
  4323,
  2194,
  1513,
  477,
  3623,
  2103,
  2850,
  1670,
  342,
  4484,
  2385,
  1967,
  1670,
  1233,
  3297,
  4104,
  1957,
  798,
  3873,
  551,
  85,
  2045,
  3962,
  3768,
  1538,
  798,
  4589,
  664,
  551,
  2993,
  1538,
  4589,
  4104,
  3297,
  1798,
  2582,
  2410,
  2645,
  3946,
  798,
  3825,
  2744,
  1670,
  1503,
  627,
  2665,
  3500,
  2194,
  4302,
  1193,
  985,
  477,
  3722,
  3946,
  798,
  3473,
  2205,
  290,
  3081,
  2929,
  2460,
  1114,
  3962,
  2103,
  5

## Embedding Representation

In [26]:
sent_length=20
embedded_docs=pad_sequences(one_hot_repr,padding='pre',maxlen=sent_length)
print(embedded_docs)

[[3333 4630  342 ... 2143 4092 2418]
 [ 427 4445 3908 ...  267 2488 1804]
 [  80 1402 3414 ... 3098 4374 4023]
 ...
 [1403 3733 4132 ... 3408 1911 1498]
 [4239 4200 4396 ... 3474 4603 4169]
 [4855 2808  793 ... 4415 3481 2670]]


In [29]:
#Creating the model
from tensorflow.keras.layers import Dropout
embedding_vector_features=40
model=Sequential()
model.add(Embedding(voc_size,embedding_vector_features,input_length=sent_length))
model.add(Dropout(0.3))
model.add(LSTM(100))
model.add(Dense(1,activation='sigmoid'))
model.compile(loss='binary_crossentropy',optimizer='adam',metrics=['accuracy'])



In [31]:
import numpy as np
X_final=np.array(embedded_docs)
y_final=np.array(y)

In [43]:
from sklearn.model_selection import train_test_split
X_train,X_test,y_train,y_test=train_test_split(X_final,y_final,test_size=0.40,random_state=42)

## Model training

In [44]:
model.fit(X_train,y_train,validation_data=(X_test,y_test),epochs=10,batch_size=64)

Epoch 1/10
172/172 [==============================] - 6s 35ms/step - loss: 0.0180 - accuracy: 0.9930 - val_loss: 0.4432 - val_accuracy: 0.9195
Epoch 2/10
172/172 [==============================] - 6s 34ms/step - loss: 0.0127 - accuracy: 0.9962 - val_loss: 0.4888 - val_accuracy: 0.9188
Epoch 3/10
172/172 [==============================] - 6s 34ms/step - loss: 0.0108 - accuracy: 0.9969 - val_loss: 0.5058 - val_accuracy: 0.9141
Epoch 4/10
172/172 [==============================] - 6s 34ms/step - loss: 0.0108 - accuracy: 0.9963 - val_loss: 0.5092 - val_accuracy: 0.9165
Epoch 5/10
172/172 [==============================] - 6s 34ms/step - loss: 0.0078 - accuracy: 0.9978 - val_loss: 0.5334 - val_accuracy: 0.9176
Epoch 6/10
172/172 [==============================] - 6s 34ms/step - loss: 0.0068 - accuracy: 0.9976 - val_loss: 0.5135 - val_accuracy: 0.9188
Epoch 7/10
172/172 [==============================] - 6s 34ms/step - loss: 0.0080 - accuracy: 0.9971 - val_loss: 0.5335 - val_accuracy: 0.9193

## Performance Metrics and Accuracy

In [45]:
y_pred=model.predict_classes(X_test)

In [46]:
from sklearn.metrics import confusion_matrix
confusion_matrix(y_test,y_pred)


array([[3829,  304],
       [ 323, 2858]], dtype=int64)

In [47]:
from sklearn.metrics import accuracy_score
accuracy_score(y_test,y_pred)

0.9142739950779327